# DL Pipeline

In [40]:
!nvidia-smi

Sat Feb  6 18:41:11 2021       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 460.39       Driver Version: 418.67       CUDA Version: 10.1     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  Tesla P100-PCIE...  Off  | 00000000:00:04.0 Off |                    0 |
| N/A   31C    P0    30W / 250W |    977MiB / 16280MiB |      0%      Default |
|                               |                      |                 ERR! |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

In [2]:
# Clone the entire repo.
!git clone -l -s git://github.com/ZackPashkin/ocr_pytorch.git
!ls

Cloning into 'ocr_pytorch'...
remote: Enumerating objects: 252, done.
remote: Counting objects: 100% (252/252), done.
remote: Compressing objects: 100% (181/181), done.
remote: Total 252 (delta 136), reused 160 (delta 55), pack-reused 0
Receiving objects: 100% (252/252), 174.32 KiB | 8.72 MiB/s, done.
Resolving deltas: 100% (136/136), done.
ocr_pytorch  sample_data


In [41]:
!wget https://storage.googleapis.com/comptech2021-ocr/synth_dataset.zip
!unzip -qq /content/synth_dataset.zip -d /content/

--2021-02-06 18:44:48--  https://storage.googleapis.com/comptech2021-ocr/synth_dataset.zip
Resolving storage.googleapis.com (storage.googleapis.com)... 74.125.142.128, 74.125.195.128, 2607:f8b0:400e:c09::80, ...
Connecting to storage.googleapis.com (storage.googleapis.com)|74.125.142.128|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 2458881188 (2.3G) [application/zip]
Saving to: ‘synth_dataset.zip’

synth_dataset.zip   100%[===================>]   2.29G  82.8MB/s    in 51s     

2021-02-06 18:45:43 (46.2 MB/s) - ‘synth_dataset.zip’ saved [2458881188/2458881188]



In [3]:
# download real dataset 
!wget https://storage.googleapis.com/comptech2021-ocr/real_dataset.zip
!unzip -qq /content/real_dataset.zip -d /content/

--2021-02-06 15:08:48--  https://storage.googleapis.com/comptech2021-ocr/real_dataset.zip
Resolving storage.googleapis.com (storage.googleapis.com)... 74.125.142.128, 74.125.195.128, 74.125.20.128, ...
Connecting to storage.googleapis.com (storage.googleapis.com)|74.125.142.128|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 194948883 (186M) [application/zip]
Saving to: ‘real_dataset.zip’

real_dataset.zip    100%[===================>] 185.92M  30.4MB/s    in 6.1s    

2021-02-06 15:08:56 (30.4 MB/s) - ‘real_dataset.zip’ saved [194948883/194948883]



In [4]:
from google.colab import drive
drive.mount('/content/gdrive/')

Mounted at /content/gdrive/


**Проверка сохранения файла, запустите ячейку и посмотрите, появился новый файл у вас**

In [ ]:
gdrive_path = "gdrive/My Drive/" 
filename = gdrive_path + "test.txt"
with open(filename , 'w') as file:
    file.write('whatever')
!ls "gdrive/My Drive/"   

 456.png				       test.txt
'Colab Notebooks'			       test.zip
 fb5def8f9f9e5945.png			       train.zip
 Meter-reading-YOLOv4-Roboflow-PyTorch.ipynb   xs.png
 old_hacks				       yolo_checkpoints
 sleep_checkpoints			      'Дейл Карнеги.docx'


In [5]:
%pip install wandb -q
import wandb
wandb.login()

     |████████████████████████████████| 2.0MB 9.3MB/s 
     |████████████████████████████████| 133kB 50.8MB/s 
     |████████████████████████████████| 102kB 12.8MB/s 
     |████████████████████████████████| 163kB 39.6MB/s 
     |████████████████████████████████| 71kB 10.9MB/s 


<IPython.core.display.Javascript object>

wandb: You can find your API key in your browser here: https://wandb.ai/authorize


wandb: Paste an API key from your profile and hit enter: ··········


wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc


True

In [6]:
!pip install -U albumentations

     |████████████████████████████████| 81kB 6.1MB/s 
     |████████████████████████████████| 37.6MB 76kB/s 
     |████████████████████████████████| 952kB 50.3MB/s 
  Found existing installation: imgaug 0.2.9
    Uninstalling imgaug-0.2.9:
      Successfully uninstalled imgaug-0.2.9
  Found existing installation: albumentations 0.1.12
    Uninstalling albumentations-0.1.12:
      Successfully uninstalled albumentations-0.1.12


Подготовка реальных данных

In [7]:
%%time

import glob
import os
import pandas as pd

df = pd.read_csv("real_dataset/HANDWRITTEN_5_folders.csv")
dfs = pd.read_csv("real_dataset/werner_real/annotation.csv", sep='\t', comment='#')

real_labels_dict = {}
for index,image_name in enumerate(glob.glob("real_dataset/HANDWRITTEN/*/*.png")):
  label = df.loc[df["INPUT:image"] == image_name[12:], "OUTPUT:output"]
  label = label.tolist()
  if label != []:
    tmp = 0
    #real_labels_dict.update({image_name:label[0]})
    
    for letter in label[0]:
      # (letter == '№') or (letter == 'N') or
      # (letter == '№') or (letter == '/') or (letter == 'S') => Label Classes = 91
      if (letter == '/') or (letter == '№') or (letter == 'N') or (letter == 'S') or (letter == 'I'):
        tmp = tmp + 1
    if (tmp == 0):
      real_labels_dict.update({image_name:label[0]})
    
images_with_value = {}
for index, row in dfs.iterrows():
    split_row = row['0.png,суммарный'].split(",")
    tmp = 0
    #img_path = "real_dataset/werner_real/data/" + split_row[0]
    #images_with_value.update({img_path:split_row[1]})
    
    for letter in split_row[1]:
      # (letter == '№') or (letter == 'N') or 
      # (letter == '№') or (letter == '/') or (letter == 'S') => Label Classes = 91
      if (letter == '/') or (letter == '№') or (letter == 'N') or (letter == 'S') or (letter == 'I'):
        tmp = tmp + 1
    if (tmp == 0):
      img_path = "real_dataset/werner_real/data/" + split_row[0]
      images_with_value.update({img_path:split_row[1]})
    

for index,image_name in enumerate(glob.glob("real_dataset/werner_real/data/*.png")):
  for key in images_with_value:
    if (image_name == key):
      real_labels_dict.update({key:images_with_value[key]})

print(len(real_labels_dict))

4214
CPU times: user 6.64 s, sys: 9.49 ms, total: 6.65 s
Wall time: 6.65 s


Подготовка синтетических данных

In [42]:
%%time

synth_labels_dict = {}
synth_werner_list = []
synth_werner = open('synth_dataset/werner_synthetic/annotation.txt','r')
try:
   synth_werner_list = synth_werner.read().splitlines()
finally:
   synth_werner.close()

for index in range(len(synth_werner_list)):
  img_path = "synth_dataset/werner_synthetic/content/result/" + synth_werner_list[index].partition(',')[0]
  label = synth_werner_list[index].partition(',')[2]
  synth_labels_dict.update({img_path:label})
  if index == 30000: break

print(len(synth_labels_dict))

30001
CPU times: user 60.5 ms, sys: 33.1 ms, total: 93.7 ms
Wall time: 197 ms


In [43]:
synth_werner_list = []
synth_werner = open('synth_dataset/werner_distorted/annotation.txt','r')
try:
   synth_werner_list = synth_werner.read().splitlines()
finally:
   synth_werner.close()

images_with_value = {}
for index in range(len(synth_werner_list)):
  img_path = "synth_dataset/werner_distorted/content/generated/" + synth_werner_list[index].rpartition(',')[2] + ".png"
  label = synth_werner_list[index].rpartition(',')[0]
  images_with_value.update({img_path:label})

for index,image_name in enumerate(glob.glob("synth_dataset/werner_distorted/content/generated/*.png")):
  for key in images_with_value:
    if (image_name == key):
      synth_labels_dict.update({key:images_with_value[key]})

print(len(synth_labels_dict))

30465


In [45]:
%%time

synth_kovshov = pd.read_csv("synth_dataset/kovshov_synth_labels.csv" ,sep='|', encoding = 'cp1251')

#synth_labels_dict = {}
for index, row in synth_kovshov.iterrows():
    split_row = row['1.jpg;(1839-1843), реформа'].split(";")
    img_path = "synth_dataset/kovshov_synth_images/" + split_row[0]
    synth_labels_dict.update({img_path:split_row[1]})

print(len(synth_labels_dict))

294723
CPU times: user 20.1 s, sys: 37.3 ms, total: 20.1 s
Wall time: 20.1 s


**Подключаем библиотеки**

In [8]:
import sys
sys.path.append("/content/ocr_pytorch/src")
from PIL import Image, ImageOps
import cv2
import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline

**config.py**

In [32]:
import glob
import os
from sklearn import preprocessing
import numpy as np

BATCH_SIZE = 8
# Synthetic or Real
DATASET_TYPE = "Real"
DATASET_LEN = 0
IMAGE_WIDTH = 512
IMAGE_HEIGHT = 64
NUM_WORKERS = 4
EPOCHS = 225
DEVICE = 'cuda'
SEED = 2020
TEST_SIZE = 0.12
#LR = 0.1
LR = 0.00035

labels_dict = {}

if DATASET_TYPE == "Real":
  labels_dict = real_labels_dict
  DATASET_LEN = len(real_labels_dict)
else:
  labels_dict = synth_labels_dict
  DATASET_LEN = len(synth_labels_dict)

**Padding изображений**

In [11]:
def resize_with_padding(img, expected_size):
    img.thumbnail((expected_size[0], expected_size[1]))
    # print(img.size)
    delta_width = expected_size[0] - img.size[0]
    delta_height = expected_size[1] - img.size[1]
    pad_width = delta_width // 2
    pad_height = delta_height // 2
    padding = (pad_width, pad_height, delta_width - pad_width, delta_height - pad_height)
    return ImageOps.expand(img, padding)

**label_encoding.py**

In [33]:
IMAGES = list(labels_dict.keys())
# to look like '6bnnm'
LABELS_NAMES = list(labels_dict.values())
# to look like ['g', 'p', 'x', 'n', 'g']
LABELS_NAMES = [[_ for _ in x] for x in LABELS_NAMES]
print(LABELS_NAMES)
LABELS_NAMES_FLAT = [_ for sublist in LABELS_NAMES for _ in sublist]
print(LABELS_NAMES_FLAT)
labels_encoded = preprocessing.LabelEncoder()
labels_encoded.fit(LABELS_NAMES_FLAT)
print(labels_encoded.classes_)
print(len(labels_encoded.classes_))
# keep 0 for unknown
LABELS_ENCODED = np.array([labels_encoded.transform(x) for x in LABELS_NAMES]) +1
#print(LABELS_ENCODED)

[['6', ' ', 'Я', 'н', 'в', 'а', 'р', 'я', ' ', '2', '0', '0', '6'], ['в', ' ', 'с', 'л', 'у', 'ч', 'а', 'е', ',', ' ', 'е', 'с', 'л', 'и'], ['м', 'е', 'т', 'о', 'д', 'и', 'ч', 'е', 'с', 'к', 'и', 'е', ' ', 'р', 'е', 'к', 'о', 'м', 'е', 'н', 'д', 'а', 'ц', 'и', 'и', '.'], ['В', 'а', 'л', 'ю', 'т', 'а'], ['У', 'р', 'б', 'а', 'н', 'и', 'з', 'а', 'ц', 'и', 'я'], ['1', ' ', 'Д', 'е', 'к', 'а', 'б', 'р', 'я', ' ', '2', '0', '0', '0'], ['С', 'о', 'б', 'о', 'л', 'е', 'в', ' ', 'Г', 'е', 'о', 'р', 'г', 'и', 'й'], ['в', ' ', 'у', 'с', 'т', 'а', 'н', 'о', 'в', 'л', 'е', 'н', 'н', 'о', 'м', ' ', 'п', 'о', 'р', 'я', 'д', 'к', 'е'], ['С', 'у', 'к', 'и', 'н', ' ', 'А', 'р', 'х', 'и', 'п', ' ', 'Т', 'а', 'р', 'а', 'с', 'о', 'в', 'и', 'ч'], ['з', 'а', 'п', 'а', 'т', 'е', 'н', 'т', 'о', 'в', 'а', 'н', 'н', 'ы', 'й', ' '], ['п', 'р', 'о', 'и', 'з', 'в', 'о', 'д', 'с', 'т', 'в', 'о'], ['д', 'о', 'м', '.', ' ', 'т', 'е', 'л', '.', ':', '5', '3', '-', '4', '8', '-', '8', '2'], ['Р', 'а', 'д', 'и', 'о', 'м',

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:14: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray
  


**dataset.py**

In [34]:
import torch 
import numpy as np
from albumentations import *

from PIL import Image

class OcrDataset: 
    """
    Handle images for dataloader.
    Apply resize and augmentations.
    Put attention to resize PIL: first goes width then height
    """
    
    def __init__(self, image_path, labels, resize=None):
        self.image_path = image_path
        self.labels = labels
        self.resize = resize
        self.augmentations = Compose(
            [
            Normalize(always_apply=True),
            Rotate(limit=(-5, 5),p=0.6),
            # OneOf([
            #       ToSepia(p=1),
            #        ToGray(p=1),
            #   ]),
            # MedianBlur(blur_limit=5, p=0.2),
            # GaussianBlur(p=0.2),
            # MotionBlur(p=0.2),
            # GaussNoise(var_limit=5. / 255., p=0.2),
            # MultiplicativeNoise(p=0.2),
            # Cutout(num_holes=8, max_h_size=10, max_w_size=10,p=0.2),
            # CoarseDropout(max_holes=8, max_height=10, max_width=10,p=0.2),
            # GridDistortion(p=0.2),
            ElasticTransform(sigma=5, alpha=0.1, alpha_affine=1, p=0.4),
            # RandomBrightness(p=0.2),
            # RandomContrast(p=0.2),
            # RandomBrightnessContrast(p=0.2),
            # IAAPiecewiseAffine(p=0.2),
            # ShiftScaleRotate(shift_limit=0.1,
            #                     scale_limit=0.1,
            #                     rotate_limit=30,
            #                     p=0.2)             
            ]                                    
                                            
                                            )
        
    def __len__(self):
        return len(self.image_path)
        
    def __getitem__(self, item):
        image = Image.open(self.image_path[item]).convert('RGB')
        labels = self.labels[item]

        image = resize_with_padding(image, (IMAGE_WIDTH, IMAGE_HEIGHT))
        
        image = np.array(image)
        augmented_image = self.augmentations(image=image)
        image = augmented_image["image"]
        image = np.transpose(image,(2,0,1)).astype(np.float32)
        
        return {
            "images": torch.tensor(image, dtype=torch.float),
            "labels": torch.tensor(labels, dtype=torch.long),
            "len_labels": len(labels)
        }



class TextCollate():
    def __call__(self, batch):
        x_padded = []
        bs = len(batch)
        max_y_len = max([i['labels'].size(0) for i in batch])
        y_padded = torch.LongTensor(len(batch), max_y_len)
        y_padded.zero_()
        len_labels = torch.zeros((bs,1), dtype=torch.int32)
 
        for i in range(len(batch)):
            x_padded.append(batch[i]['images'].unsqueeze(0))
            y = batch[i]['labels']
            len_labels[i,0]= len(y)
            y_padded[i, :y.size(0)] = y
 
        x_padded = torch.cat(x_padded)
        return {'images': x_padded,
                'labels': y_padded,
                'len_labels':len_labels}

**model.py**

In [35]:
import torch
import torch.nn as nn
from torch.nn import functional as F
from torchvision import models

class OcrModel_v0(nn.Module):
    def __init__(self, num_characters):
        super(OcrModel_v0, self).__init__()
        self.conv1 = nn.Conv2d(3,128, kernel_size=(3,3), padding=(1,1))
        self.maxpool1 = nn.MaxPool2d(kernel_size=(2,2))
        self.conv2 = nn.Conv2d(128,64, kernel_size=(3,3), padding=(1,1))
        self.maxpool2 = nn.MaxPool2d(kernel_size=(2,2))
        self.linear1 = nn.Linear(1024, 64)
        self.dropout1  = nn.Dropout(0.2)
        self.gru = nn.GRU(64, 32 , bidirectional=True,
                          num_layers=2,
                          batch_first=True)
        self.output = nn.Linear(64, num_characters + 1)
        
    def forward(self, images,len_labels=None, labels=None):
        bs, c, h, w = images.size()
        #print(bs, c, h, w)
        x = F.relu(self.conv1(images))
        #print(x.size())
        x = self.maxpool1(x)
        #print(x.size()) 
        x = F.relu(self.conv2(x))
        #print(x.size())
        x = self.maxpool2(x)
        # need to change channels for rnn bs, f, h, w --> bs, w, f, h
        x = x.permute(0,3,1,2)
        #print(x.size())
        x = x.view(bs, x.size(1),-1)
        #print(x.size()[2])
        x = self.linear1(x)
        x = self.dropout1(x)
        #print(x.size())
        x, _ = self.gru(x)
        #print(x.size())
        x = self.output(x)
        #print(x.size())
        # permute again 
        x = x.permute(1,0,2)
        #print(x.size())
        if labels is not None: 
            log_softmax_values =  F.log_softmax(x,2)   
            input_lenghts = torch.full(size=(bs,),
                                       fill_value=log_softmax_values.size(0), 
                                       dtype = torch.int32
                                       )
            #print(input_lenghts)
            
            output_lenghts = len_labels

            #print(output_lenghts)
            #print(labels.size())
            
            loss = nn.CTCLoss(blank=0,zero_infinity = True)(
                log_softmax_values,
                labels,
                input_lenghts,
                output_lenghts
            )  
            
            return x, loss
        return x

class ResNetOCR(nn.Module):
  def __init__(self, n_classes, hidden_rnn):
    super(ResNetOCR,self).__init__()
    model = nn.Sequential(*list(models.resnet18(pretrained=False).children())[:-4])
    self.fc1 = nn.Linear(1024, hidden_rnn)
    self.cnn = model
    self.rnn = nn.GRU(hidden_rnn, 32 , bidirectional=True,
                          num_layers=2,
                          batch_first=True)
    '''
    self.rnn = nn.GRU(hidden_rnn, 64 , bidirectional=True,
                          num_layers=3,
                          batch_first=True)
    '''
    self.output = nn.Linear(64,n_classes+1)
  
  def forward(self, images, labels=None, len_labels = None):
    bs, c, h, w = images.size()
    x = self.cnn(images)
    #print(x.size())
    x = x.permute(0,3,1,2)
    #print(x.size())
    x = x.view(bs, x.size(1),-1)
    #print(x.size()[2])
    x = self.fc1(x)
    x, _ = self.rnn(x)
    #print(x.size()[2])
    x = self.output(x)
    #print(x.size())
    # permute again 
    x = x.permute(1,0,2)
    #print(x)
    if labels is not None:
      log_softmax_values =  F.log_softmax(x,2)   
      input_lenghts = torch.full(size=(bs,),
                                 fill_value=log_softmax_values.size(0), 
                                 dtype = torch.int32
                                 )
      #print(input_lenghts)
         
      loss = nn.CTCLoss(blank=0,zero_infinity = True)(
          log_softmax_values,
          labels,
          input_lenghts,
          len_labels
      )  
      
      return x, loss
    return x



class BidirectionalLSTM(nn.Module):

    def __init__(self, nIn, nHidden, nOut):
        super(BidirectionalLSTM, self).__init__()

        self.rnn = nn.LSTM(nIn, nHidden, bidirectional=True)
        self.embedding = nn.Linear(nHidden * 2, nOut)

    def forward(self, input):
        recurrent, _ = self.rnn(input)
        T, b, h = recurrent.size()
        t_rec = recurrent.view(T * b, h)

        output = self.embedding(t_rec)  # [T * b, nOut]
        output = output.view(T, b, -1)

        return output


class CRNN(nn.Module):

    def __init__(self, imgH, nc, nclass, nh, n_rnn=2, leakyRelu=False):
        super(CRNN, self).__init__()
        assert imgH % 16 == 0, 'imgH has to be a multiple of 16'

        ks = [3, 3, 3, 3, 3, 3, 2, 2]
        ps = [1, 1, 1, 1, 1, 1, 0, 0]
        ss = [1, 1, 1, 1, 1, 1, 1, 1]
        nm = [64, 128, 256, 256, 512, 512, 512, 512]

        cnn = nn.Sequential()

        def convRelu(i, batchNormalization=False):
            nIn = nc if i == 0 else nm[i - 1]
            nOut = nm[i]
            cnn.add_module('conv{0}'.format(i),
                           nn.Conv2d(nIn, nOut, ks[i], ss[i], ps[i]))
            if batchNormalization:
                cnn.add_module('batchnorm{0}'.format(i), nn.BatchNorm2d(nOut))
            if leakyRelu:
                cnn.add_module('relu{0}'.format(i),
                               nn.LeakyReLU(0.2, inplace=True))
            else:
                cnn.add_module('relu{0}'.format(i), nn.ReLU(True))

        convRelu(0)
        cnn.add_module('pooling{0}'.format(0), nn.MaxPool2d(2, 2))  # 64x16x64
        convRelu(1)
        cnn.add_module('pooling{0}'.format(1), nn.MaxPool2d(2, 2))  # 128x8x32
        convRelu(2, True)
        convRelu(3)
        cnn.add_module('pooling{0}'.format(2),
                       nn.MaxPool2d((2, 2), (2, 1), (0, 1)))  # 256x4x16
        convRelu(4, True)
        convRelu(5)
        cnn.add_module('pooling{0}'.format(3),
                       nn.MaxPool2d((2, 2), (2, 1), (0, 1)))  # 512x2x16
        convRelu(6, True)  # 512x1x16

        cnn.add_module('pooling{0}'.format(4),
                       nn.MaxPool2d((2, 2), (2, 1), (0, 1)))  # 512x2x16
        #convRelu(7, True)  # 512x1x16


        self.cnn = cnn
        self.rnn = nn.Sequential(
            BidirectionalLSTM(512, nh, nh),
            BidirectionalLSTM(nh, nh, nclass))


    def forward(self, images, labels=None, len_labels = None):
        # conv features
        conv = self.cnn(images)
        b, c, h, w = conv.size()
        #assert h == 1, "the height of conv must be 1"
        conv = conv.squeeze(2)
        #print(conv.size())
        print(conv.size())
        conv = conv.permute(2, 0, 1)  # [w, b, c]

        # rnn features
        output = self.rnn(conv)
        
        # add log_softmax to converge output
        x = output
        print(x.size())
        if labels is not None: 
            log_softmax_values =  F.log_softmax(x,2)   
            input_lenghts = torch.full(size=(b,),
                                       fill_value=log_softmax_values.size(0), 
                                       dtype = torch.int32
                                       )
            loss = nn.CTCLoss(blank=0,zero_infinity = True)(
                log_softmax_values,
                labels,
                input_lenghts,
                len_labels
            )  
            
            return x, loss

        return x


class OcrModel_mobilenet(nn.Module):
    def __init__(self, num_characters):
        super(OcrModel_mobilenet, self).__init__()
        mobilenet = models.mobilenet_v2()
        self.mobilenet_feature_extractor = nn.Sequential(*list(mobilenet.children())[:-1])
        self.linear1 = nn.Linear(int(20480/64), 64)
        self.dropout1  = nn.Dropout(0.2)
        self.gru = nn.GRU(64, 32 , bidirectional=True,
                          num_layers=2,
                          dropout=0.25,
                          batch_first=True)
        self.output = nn.Linear(64, num_characters + 1)
        
    def forward(self, images, labels=None, len_labels=None):
        bs, c, h, w = images.size()
        out = F.relu(self.mobilenet_feature_extractor(images))# 32 1280 7 7
        #print(out.size())

        x = out.permute(0,3,1,2) # 32 10, 1280, 3
        #print(x.size())
        x = torch.reshape(x,(bs, 64, int(20480/64)))#32 49 1280
        #print(x.size())
        x = self.linear1(x)
        x = self.dropout1(x)
        #print(x.size())


        x, _ = self.gru(x)
        #print(x.size())
        x = self.output(x)
        #print(x.size())
        # permute again 
        x = x.permute(1,0,2)
        #print(x.size())
        if labels is not None: 
            log_softmax_values =  F.log_softmax(x,2)   
            input_lenghts = torch.full(size=(bs,),
                                       fill_value=log_softmax_values.size(0), 
                                       dtype = torch.int32
                                       )
            #print(input_lenghts)
            
            loss = nn.CTCLoss(blank=0,zero_infinity = True)(
                log_softmax_values,
                labels,
                input_lenghts,
                len_labels
            )  
            
            return x, loss
        return x


class OcrModel_vgg16(nn.Module):
    def __init__(self, num_characters):
        super(OcrModel_vgg16, self).__init__()
        vgg = models.vgg16_bn(pretrained=True)
        self.vgg_feature_extractor = nn.Sequential(*list(vgg.children())[:-1])
        self.linear1 = nn.Linear(256, 64)
        self.dropout1  = nn.Dropout(0.2)
        self.gru = nn.GRU(64, 32 , bidirectional=True,
                          num_layers=2,
                          dropout=0.25,
                          batch_first=True)
        self.output = nn.Linear(64, num_characters + 1)
        
    def forward(self, images, labels=None, len_labels=None):
        bs, c, h, w = images.size()
        out = F.relu(self.vgg_feature_extractor(images))
        #print(out.size())

        x = out.permute(0,3,1,2) # 32 7 512  7 
        #print(x.size()) #512 7 7 
        x = torch.reshape(x,(bs, 7*7*2, 256))#view(bs, 7*7*2, 256)  # 32 7 512*7 
        #print(x.size()[2])
        x = self.linear1(x)
        x = self.dropout1(x)
        #print(x.size())


        x, _ = self.gru(x)
        #print(x.size())
        x = self.output(x)
        #print(x.size())
        # permute again 
        x = x.permute(1,0,2)
        #print(x.size())
        if labels is not None: 
            log_softmax_values =  F.log_softmax(x,2)   
            input_lenghts = torch.full(size=(bs,),
                                       fill_value=log_softmax_values.size(0), 
                                       dtype = torch.int32
                                       )
           
            loss = nn.CTCLoss(blank=0, zero_infinity = True)(
                log_softmax_values,
                labels,
                input_lenghts,
                len_labels)
            
            return x, loss
        return x

**train_utils.py**

In [36]:
#from tqdm import tqdm
import torch

def train(model, dataloader, optimizer, scaler): 
    model.train()
    final_loss = 0
    tracker = tqdm(dataloader, total=len(dataloader))
    for data in tracker:
        for key, value in data.items():
            data[key] = value.to(DEVICE)
        optimizer.zero_grad()

        with torch.cuda.amp.autocast():
          _, loss = model(**data)
        
        scaler.scale(loss).backward()
        scaler.step(optimizer)
        scaler.update()

        final_loss += loss.item()
    return final_loss / len(dataloader)
    

def evaluate(model, dataloader, scaler):
    model.eval()
    final_loss = 0
    final_predictions = []
    tracker = tqdm(dataloader, total=len(dataloader))
    # if you have out of memory error put torch.no_grad()
    with torch.no_grad():
        for data in tracker:
            for key, value in data.items():
                data[key] = value.to(DEVICE)
            
            with torch.cuda.amp.autocast():
              batch_predictions, loss = model(**data)
            
            final_predictions.append(batch_predictions)
            final_loss += loss.item()
        return final_predictions, final_loss / len(dataloader)

def transform_timeseries_string(batch):
    new_batch = []
    for string in batch:
        new_string = []
        last_symbol = '*'
        for symbol in string:
            if symbol == '*':
                pred_symbol = ''
            elif symbol == last_symbol:
                pass
            else:
                new_string.append(symbol)
                last_symbol = symbol
        new_batch.append(new_string)
    return new_batch


def sybol_wise_accuracy(true, pred):
    num_true_symbol = 0
    for index in range(min(len(true), len(pred))):
        if pred[index] == true[index]:
            num_true_symbol += 1
    return num_true_symbol / len(true)


def sybol_wise_accuracy_batch(true, pred):
    acc = 0.0
    for batch_ind in range(len(true)):
        acc += sybol_wise_accuracy(true[batch_ind], pred[batch_ind])
    return acc / len(true)


def string_wise_accuracy_batch(pred, true):
    num_correct_strings = 0
    for batch_ind in range(len(true)):
        if ''.join(pred[batch_ind]) == ''.join(true[batch_ind]):
            num_correct_strings += 1
    return num_correct_strings / len(true)

**train.py**

In [38]:
import datetime
import torch
import wandb # weights & Biases
import numpy as np

from sklearn import model_selection
from sklearn import metrics

from decode_predictions import decode_preds

from pprint import pprint
from tqdm import tqdm_notebook as tqdm

torch.manual_seed(SEED)
torch.cuda.manual_seed_all(SEED)
torch.backends.cudnn.deterministic = True
torch.backends.cudnn.benchmark = True
np.random.seed(SEED)
os.environ['PYTHONHASHSEED'] = str(SEED)


def fit():
    (
        train_img,
        test_img, 
        train_labels, 
        test_labels, 
        train_orig_labels, 
        test_orig_targets,
    )   =model_selection.train_test_split(
            IMAGES, LABELS_ENCODED, LABELS_NAMES, test_size=TEST_SIZE, random_state=SEED)
    
    train_dataset = OcrDataset(image_path=train_img, 
                               labels=train_labels, 
                               resize=(IMAGE_HEIGHT,IMAGE_WIDTH)
                              )
    
    train_loader = torch.utils.data.DataLoader(
        train_dataset,
        batch_size=BATCH_SIZE,
        num_workers=NUM_WORKERS,
        collate_fn=TextCollate(),
        shuffle=True
    )
    
    
    test_dataset = OcrDataset(image_path=test_img, 
                               labels=test_labels, 
                               resize=(IMAGE_HEIGHT,IMAGE_WIDTH)
                              )
    
    test_loader = torch.utils.data.DataLoader(
        test_dataset,
        batch_size=BATCH_SIZE,
        num_workers=NUM_WORKERS,
        collate_fn=TextCollate(),
        shuffle=False
    )

    wandb.init(project="OCR_Baseline", config={
    "DATASET_TYPE": DATASET_TYPE,
    "DATASET_LEN": DATASET_LEN,
    "BATCH_SIZE": BATCH_SIZE,
    "EPOCHS": EPOCHS,
    "IMAGE_WIDTH": IMAGE_WIDTH,
    "IMAGE_HEIGHT": IMAGE_HEIGHT,
    "NUM_WORKERS": NUM_WORKERS,
    "SEED": SEED,
    "TEST_SIZE": TEST_SIZE,
    "LR": LR,
    "MODEL": "rn18.pt train on real dataset"
    })

    model = ResNetOCR(n_classes=len(labels_encoded.classes_),hidden_rnn=64)
    model.load_state_dict(torch.load("rn18.pt"))
    model.to(DEVICE)
    
    scaler = torch.cuda.amp.GradScaler()

    optimizer = torch.optim.Adam(model.parameters(), lr=LR)
    scheduler = torch.optim.lr_scheduler.StepLR(optimizer, step_size=21,gamma=1.1) 

    wandb.watch(model)

    best_acc = 0.55

    for epoch in range(EPOCHS):
        train_loss = train(model, train_loader, optimizer, scaler)
        valid_preds, valid_loss = evaluate(model, test_loader, scaler)
        valid_final_preds = []
        
        for pred in valid_preds:
            #print(pred)
            cur_preds = decode_preds(pred, labels_encoded)
            valid_final_preds.extend(cur_preds)

        valid_final_preds = transform_timeseries_string(valid_final_preds)
        images_prediction = []

        for index, batch in enumerate(test_dataset):
          image = batch['images']  
          image = image.squeeze().permute(1,2,0).numpy()
          pred_label = ''.join(map(str, valid_final_preds[index]))
          orig_label = ''.join(map(str, test_orig_targets[index]))
          caption = "Prediction: " + pred_label + "\n" + "Original: " + orig_label
          images_prediction.append(wandb.Image(image, caption=caption))
          # Так как мы рассматриваем 3 фотографии
          if index == 35: break
        
        show_preds_list = list(zip(test_orig_targets, valid_final_preds))[0:35]
        symbol_acc = sybol_wise_accuracy_batch(test_orig_targets, valid_final_preds)
        string_acc = string_wise_accuracy_batch(test_orig_targets, valid_final_preds)
        print(*show_preds_list, sep='\n')
        pprint("-"*90)
        wandb.log({"epoch": epoch, "train loss": train_loss, "valid loss": valid_loss, 
                   "symbol acc": symbol_acc, "string acc":string_acc,
                   "Images with prediction": images_prediction[0:35]})
        pprint(f"Epoch: {epoch} | Train loss = {train_loss} | Valid loss = {valid_loss} | symbol acc = {symbol_acc} | string acc = {string_acc} |")
        pprint("-"*90)
        #scheduler.step()
        if (symbol_acc >= best_acc):
          best_acc = symbol_acc
          torch.save(model.state_dict(), "gdrive/My Drive/Exp/model_weights.pt")

    
    return model

In [39]:
offset = datetime.timezone(datetime.timedelta(hours=3))
model = fit()
model_time = datetime.datetime.now(offset).strftime('%H:%M:%S')
torch.save(model.state_dict(), "gdrive/My Drive/Exp/model_weights_{}time.pt".format(model_time))

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:7: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  import sys


/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:28: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`



(['П', 'о', 'л', 'и', 'т', 'и', 'к', 'а'], [])
(['В', 'о', 'р', 'о', 'н', 'е', 'ж', 'с', 'к', 'а', 'я', ' ', 'о', 'б', 'л', 'а', 'с', 'т', 'ь'], ['р', ' '])
(['с', 'л', 'о', 'м', 'и', 'т', 'ь'], [])
(['3', '.', '0', '8', '.', '2', '0', '1', '8'], [])
(['М', 'о', 'д', 'е', 'л', 'ь'], [])
(['а', 'в', 'т', 'о', 'м', 'о', 'б', 'и', 'л', 'ь'], [])
(['т', 'ы', 'с', 'я', 'ч'], [])
(['З', 'а', 'я', 'в', 'л', 'е', 'н', 'и', 'е'], [])
(['с', 'у', 'д', 'е', 'б', 'н', 'ы', 'й'], [])
(['Р', 'а', 'з', 'р', 'е', 'ш', 'и', 'т', 'ь', ' ', 'м', 'н', 'е'], [])
(['н', 'а', 'в', 'е', 'с', 'т', 'и', ' ', 'п', 'о', 'р', 'я', 'д', 'о', 'к'], ['р'])
(['с', ' ', 'п', 'е', 'р', 'е', 'х', 'о', 'д', 'о', 'м'], [' '])
(['у', 'с', 'л', 'о', 'в', 'и', 'е'], [])
(['к', 'а', 'п', 'о', 'т'], [])
(['ф', 'о', 'р', 'м', 'а'], [])
(['н', 'а', 'р', 'у', 'ш', 'е', 'н', 'и', 'е', 'м', ' ', 'с', 'н', 'а'], [' '])
(['и', 'б', 'о'], [])
(['ч', 'и', 'т', 'а', 'т', 'е', 'л', 'ь'], [])
(['о', 'б', 'л', 'а', 'с', 'т', 'ь'], [])
(['Н


(['П', 'о', 'л', 'и', 'т', 'и', 'к', 'а'], [])
(['В', 'о', 'р', 'о', 'н', 'е', 'ж', 'с', 'к', 'а', 'я', ' ', 'о', 'б', 'л', 'а', 'с', 'т', 'ь'], ['р', ' '])
(['с', 'л', 'о', 'м', 'и', 'т', 'ь'], [])
(['3', '.', '0', '8', '.', '2', '0', '1', '8'], [])
(['М', 'о', 'д', 'е', 'л', 'ь'], [])
(['а', 'в', 'т', 'о', 'м', 'о', 'б', 'и', 'л', 'ь'], [])
(['т', 'ы', 'с', 'я', 'ч'], [])
(['З', 'а', 'я', 'в', 'л', 'е', 'н', 'и', 'е'], [])
(['с', 'у', 'д', 'е', 'б', 'н', 'ы', 'й'], [])
(['Р', 'а', 'з', 'р', 'е', 'ш', 'и', 'т', 'ь', ' ', 'м', 'н', 'е'], [' '])
(['н', 'а', 'в', 'е', 'с', 'т', 'и', ' ', 'п', 'о', 'р', 'я', 'д', 'о', 'к'], [' '])
(['с', ' ', 'п', 'е', 'р', 'е', 'х', 'о', 'д', 'о', 'м'], [' '])
(['у', 'с', 'л', 'о', 'в', 'и', 'е'], [])
(['к', 'а', 'п', 'о', 'т'], [])
(['ф', 'о', 'р', 'м', 'а'], [])
(['н', 'а', 'р', 'у', 'ш', 'е', 'н', 'и', 'е', 'м', ' ', 'с', 'н', 'а'], ['р', 'н', ' '])
(['и', 'б', 'о'], [])
(['ч', 'и', 'т', 'а', 'т', 'е', 'л', 'ь'], [])
(['о', 'б', 'л', 'а', 'с', 'т', '


(['П', 'о', 'л', 'и', 'т', 'и', 'к', 'а'], ['и'])
(['В', 'о', 'р', 'о', 'н', 'е', 'ж', 'с', 'к', 'а', 'я', ' ', 'о', 'б', 'л', 'а', 'с', 'т', 'ь'], ['о', 'р', 'н', 'а', ' ', 'о', 'в'])
(['с', 'л', 'о', 'м', 'и', 'т', 'ь'], ['о'])
(['3', '.', '0', '8', '.', '2', '0', '1', '8'], [])
(['М', 'о', 'д', 'е', 'л', 'ь'], [])
(['а', 'в', 'т', 'о', 'м', 'о', 'б', 'и', 'л', 'ь'], ['в'])
(['т', 'ы', 'с', 'я', 'ч'], [])
(['З', 'а', 'я', 'в', 'л', 'е', 'н', 'и', 'е'], [' ', 'е', 'и'])
(['с', 'у', 'д', 'е', 'б', 'н', 'ы', 'й'], [' '])
(['Р', 'а', 'з', 'р', 'е', 'ш', 'и', 'т', 'ь', ' ', 'м', 'н', 'е'], ['и', ' '])
(['н', 'а', 'в', 'е', 'с', 'т', 'и', ' ', 'п', 'о', 'р', 'я', 'д', 'о', 'к'], ['т', 'р', ' ', 'р', ' '])
(['с', ' ', 'п', 'е', 'р', 'е', 'х', 'о', 'д', 'о', 'м'], [' ', 'а', 'р', 'е', 'о'])
(['у', 'с', 'л', 'о', 'в', 'и', 'е'], [])
(['к', 'а', 'п', 'о', 'т'], [])
(['ф', 'о', 'р', 'м', 'а'], ['н'])
(['н', 'а', 'р', 'у', 'ш', 'е', 'н', 'и', 'е', 'м', ' ', 'с', 'н', 'а'], ['а', 'р', 'е', 'н', 

...


(['П', 'о', 'л', 'и', 'т', 'и', 'к', 'а'], ['я', 'о', 'м', 'е', 'т', 'и', 'к', 'а'])
(['В', 'о', 'р', 'о', 'н', 'е', 'ж', 'с', 'к', 'а', 'я', ' ', 'о', 'б', 'л', 'а', 'с', 'т', 'ь'], ['В', 'о', 'р', 'о', 'н', 'е', 'к', 'с', 'к', 'а', 'я', ' ', 'о', 'б', 'л', 'а', 'с', 'т', 'ь'])
(['с', 'л', 'о', 'м', 'и', 'т', 'ь'], ['с', 'л', 'ю', 'м', 'и', 'б', 'ь'])
(['3', '.', '0', '8', '.', '2', '0', '1', '8'], ['3', '9', '1', '.', '2', '0', '1', '8'])
(['М', 'о', 'д', 'е', 'л', 'ь'], ['М', 'о', 'д', 'е', 'л', 'ь'])
(['а', 'в', 'т', 'о', 'м', 'о', 'б', 'и', 'л', 'ь'], ['а', 'в', 'т', 'о', 'м', 'о', 'б', 'ь'])
(['т', 'ы', 'с', 'я', 'ч'], ['т', 'о', 'л', ' ', 'а', 'я', 'г'])
(['З', 'а', 'я', 'в', 'л', 'е', 'н', 'и', 'е'], ['З', 'а', 'я', 'в', 'л', 'е', 'н', 'и', 'е'])
(['с', 'у', 'д', 'е', 'б', 'н', 'ы', 'й'], ['с', 'л', 'у', 'д', 'е', 'б', 'ы', 'й'])
(['Р', 'а', 'з', 'р', 'е', 'ш', 'и', 'т', 'ь', ' ', 'м', 'н', 'е'], ['Р', 'о', 'у', 'е', 'н', 'м', 'а', 'т', 'ь', ' ', 'н', 'л', 'е'])
(['н', 'а', 'в


(['П', 'о', 'л', 'и', 'т', 'и', 'к', 'а'], ['П', 'о', 'м', 'е', 'т', 'и', 'к', 'а'])
(['В', 'о', 'р', 'о', 'н', 'е', 'ж', 'с', 'к', 'а', 'я', ' ', 'о', 'б', 'л', 'а', 'с', 'т', 'ь'], ['В', 'о', 'р', 'о', 'н', 'ь', 'с', 'к', 'с', 'к', 'а', 'я', ' ', 'о', 'б', 'л', 'а', 'с', 'т', 'ь'])
(['с', 'л', 'о', 'м', 'и', 'т', 'ь'], ['с', 'л', 'о', 'м', 'и', 'б', 'ь'])
(['3', '.', '0', '8', '.', '2', '0', '1', '8'], ['2', '3', '.', '2', '1', '.', '2', '0', '1', '8'])
(['М', 'о', 'д', 'е', 'л', 'ь'], ['М', 'о', 'д', 'е', 'л', 'ь'])
(['а', 'в', 'т', 'о', 'м', 'о', 'б', 'и', 'л', 'ь'], ['а', 'в', 'т', 'о', 'м', 'о', 'б', 'ы', 'ь'])
(['т', 'ы', 'с', 'я', 'ч'], ['т', 'п', 'л', 'а', 'я', 'г'])
(['З', 'а', 'я', 'в', 'л', 'е', 'н', 'и', 'е'], ['З', 'а', 'я', 'в', 'л', 'е', 'н', 'и', 'е'])
(['с', 'у', 'д', 'е', 'б', 'н', 'ы', 'й'], ['с', 'л', 'е', 'д', 'о', 'б', 'ш', 'ы', 'й'])
(['Р', 'а', 'з', 'р', 'е', 'ш', 'и', 'т', 'ь', ' ', 'м', 'н', 'е'], ['Б', 'о', 'д', 'е', 'н', 'и', 'т', 'ь', ' ', 'н', 'а', 'е'])


(['П', 'о', 'л', 'и', 'т', 'и', 'к', 'а'], ['П', 'о', 'м', 'т', 'и', 'к', 'а'])
(['В', 'о', 'р', 'о', 'н', 'е', 'ж', 'с', 'к', 'а', 'я', ' ', 'о', 'б', 'л', 'а', 'с', 'т', 'ь'], ['В', 'о', 'р', 'о', 'н', 'с', 'к', 'а', 'я', ' ', 'о', 'б', 'л', 'а', 'с', 'т', 'ь'])
(['с', 'л', 'о', 'м', 'и', 'т', 'ь'], ['с', 'л', 'о', 'м', 'и', 'й', 'ь'])
(['3', '.', '0', '8', '.', '2', '0', '1', '8'], ['3', '.', '9', '1', '.', '2', '0', '9', '1'])
(['М', 'о', 'д', 'е', 'л', 'ь'], ['М', 'о', 'д', 'е', 'л', 'ь'])
(['а', 'в', 'т', 'о', 'м', 'о', 'б', 'и', 'л', 'ь'], ['а', 'в', 'т', 'о', 'м', 'о', 'б', 'ы', 'ь'])
(['т', 'ы', 'с', 'я', 'ч'], ['т', 'л', 'с', 'я', 'г'])
(['З', 'а', 'я', 'в', 'л', 'е', 'н', 'и', 'е'], ['З', 'а', 'я', 'в', 'л', 'е', 'н', 'и', 'е'])
(['с', 'у', 'д', 'е', 'б', 'н', 'ы', 'й'], ['с', 'л', 'е', 'д', 'о', 'н', 'ы', 'й'])
(['Р', 'а', 'з', 'р', 'е', 'ш', 'и', 'т', 'ь', ' ', 'м', 'н', 'е'], ['Р', 'е', 'д', 'е', 'и', 'с', 'т', 'ь', ' ', 'н', 'т', 'и', 'т', 'е'])
(['н', 'а', 'в', 'е', 'с


(['П', 'о', 'л', 'и', 'т', 'и', 'к', 'а'], ['1', ')', 'о', 'м', 'т', 'и', 'к', 'а'])
(['В', 'о', 'р', 'о', 'н', 'е', 'ж', 'с', 'к', 'а', 'я', ' ', 'о', 'б', 'л', 'а', 'с', 'т', 'ь'], ['В', 'о', 'р', 'о', 'н', 'е', 'к', 'с', 'к', 'а', 'я', ' ', 'о', 'б', 'л', 'а', 'с', 'т', 'ь'])
(['с', 'л', 'о', 'м', 'и', 'т', 'ь'], ['с', 'л', 'о', 'и', 'й', 'ь'])
(['3', '.', '0', '8', '.', '2', '0', '1', '8'], ['3', '.', '9', '1', '.', '2', '0', '1'])
(['М', 'о', 'д', 'е', 'л', 'ь'], ['М', 'о', 'д', 'е', 'л', 'ь'])
(['а', 'в', 'т', 'о', 'м', 'о', 'б', 'и', 'л', 'ь'], ['а', 'в', 'т', 'о', 'м', 'о', 'б', 'ы', 'л', 'ь'])
(['т', 'ы', 'с', 'я', 'ч'], ['т', 'о', 'л', ' ', 'а', 'я', 'г'])
(['З', 'а', 'я', 'в', 'л', 'е', 'н', 'и', 'е'], ['З', 'а', 'я', 'в', 'л', 'е', 'н', 'и', 'е'])
(['с', 'у', 'д', 'е', 'б', 'н', 'ы', 'й'], ['с', 'л', 'у', 'д', 'о', 'д', 'ы', 'й'])
(['Р', 'а', 'з', 'р', 'е', 'ш', 'и', 'т', 'ь', ' ', 'м', 'н', 'е'], ['Г', 'Р', 'о', 'д', 'е', 'н', 'т', 'а', 'т', 'ь', ' ', 'т', 'е'])
(['н', 'а


(['П', 'о', 'л', 'и', 'т', 'и', 'к', 'а'], ['П', 'о', 'м', 'т', 'и', 'к', 'а'])
(['В', 'о', 'р', 'о', 'н', 'е', 'ж', 'с', 'к', 'а', 'я', ' ', 'о', 'б', 'л', 'а', 'с', 'т', 'ь'], ['В', 'о', 'р', 'о', 'н', 'е', 'ж', 'к', 'с', 'к', 'а', 'я', ' ', 'о', 'б', 'л', 'а', 'с', 'т', 'ь'])
(['с', 'л', 'о', 'м', 'и', 'т', 'ь'], ['с', 'л', 'о', 'м', 'и', 'й', 'ь'])
(['3', '.', '0', '8', '.', '2', '0', '1', '8'], ['3', '.', 'я', '1', '.', '2', '0', '1'])
(['М', 'о', 'д', 'е', 'л', 'ь'], ['М', 'о', 'д', 'е', 'л', 'ь'])
(['а', 'в', 'т', 'о', 'м', 'о', 'б', 'и', 'л', 'ь'], ['а', 'в', 'о', 'м', 'о', 'б', 'ы', 'ь'])
(['т', 'ы', 'с', 'я', 'ч'], ['т', 'а', 'л', ' ', 'а', 'я', 'г'])
(['З', 'а', 'я', 'в', 'л', 'е', 'н', 'и', 'е'], ['з', 'а', 'я', 'в', 'л', 'е', 'н', 'и', 'е'])
(['с', 'у', 'д', 'е', 'б', 'н', 'ы', 'й'], ['с', 'л', 'е', 'д', 'о', 'б', 'ш', 'ы', 'й'])
(['Р', 'а', 'з', 'р', 'е', 'ш', 'и', 'т', 'ь', ' ', 'м', 'н', 'е'], ['Р', 'о', 'д', 'е', 'н', 'с', 'т', 'ь', ' ', 'н', 'л', 'е'])
(['н', 'а', 'в

**После обучения почистите у GPU память**

In [25]:
import gc 

In [26]:
gc.collect()
torch.cuda.empty_cache()

In [27]:
!nvidia-smi

Sat Feb  6 16:19:30 2021       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 460.39       Driver Version: 418.67       CUDA Version: 10.1     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  Tesla P100-PCIE...  Off  | 00000000:00:04.0 Off |                    0 |
| N/A   33C    P0    30W / 250W |    853MiB / 16280MiB |      0%      Default |
|                               |                      |                 ERR! |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------